# Sélection de variables pour la régression

Le but de ce TP est d'implémenter divers algorithmes pour sélectionner uniquement les variables les plus importantes pour un problème de régression. Ces méthodes servent pour améliorer la performance d'un modèle tout en réduisant sa complexité

| Numéro        | Compétence           | 
|:------------- |:--------------------:|
|RL206|	Comprendre la définition du Cp de Mallows|
|RL207|	Etre capable de définir un algorithme de sélection de modèle donné un critère |
|PY503|	Savoir implémenter un algorithme itératif de sélection de variables|


## Ex. 1 — De l’importance des variables

Récupérez le fichier cereal.mat sur moodle. Ce fichier contient les mesures des ingrédients de céréales pour petit déjeuner. Sur chaque type de céréale, 8 variables ont été mesurées. Ces variables sont (dans l’ordre) :
- Calories: la teneur en calories (le nombre pour un repas)
- Carbo: la teneur en carbohydrates (en gramme pour un repas)
- Cups: le nombre de tasse recommandé par repas
- Fat: la teneur en graisse (en gramme pour un repas)
- Fiber: la teneur en fibres alimentaires (en gramme pour un repas)
- Potass: la teneur en potassium (en mg pour un repas)
- Protein: la teneur en proteine (en gramme pour un repas)
- Sugars: la teneur en sucre (en gramme pour un repas)
    
Ce fichier peut se décomposer en une matrice `X` qui contient toutes les données, et le tableau `Name` qui contient les noms des marques.

À chaque type de céréale a été associé son nom contenu dans la variable Name. Ainsi la première céréale est mat["name"][0] -> ’100% Bran’.

1) Afin de déterminer quelle est la variable la plus importante pour la régression linéaire, effectuer 7 régressions linéaire simple de chacune des autres variables contre  La variable FAT.

On commence par charger les données du fichier "cereal.mat" et construire la matrice `X` du modèle complet et le vecteur `y` de la variable à expliquer. Vous pouvez jeter un oeil au fichier à l'entete du fichier `cereal.mat`.

In [ ]:
import scipy.io as sio
import numpy as np
mat = sio.loadmat("cereal.mat")
X = mat["X"]
y = X[:, 3] # la quatrieme colonne
X = np.delete(X, 3, 1)
np.unique(y)

b. Constuire une matrice A permettrant de stocker les paramètres de tous les modèles, ainsi qu'un vecteur $s2$ et un vecteur $R2$ permettant de stocker les $S^2$ et $R^2$ de tous les modèles que l'on souhaite tester.

**aide** : `np.zeros`

In [ ]:
A = np.zeros((p,2))
s2 = np.zeros((p,))
R2 = np.zeros((p,))

In [ ]:
A = ...
s2 = ...
R2 = ...

c. En utilisant la fonction `ma_reg` du précédent TP, calculez les paramètres, les $S^2$ (variance non biaisée) et les $R^2$ (coefficient de détermination) de tous les modèles. 

Retrouvez quelle est la variable la plus importante au sens du $R^2$

**aide** `np.argmax` renvoie l'indice du max plutot que la valeur du max

In [ ]:
for i in range(p):
    Xn = ...
    A[i,:], s2[i], R2[i], diagd = ...

with np.printoptions(precision=3, suppress=True):
    print('Erreur résiduelle :',s2) 
    print('               R2 :',R2)

v = ...
ind = ...

print(f"Le plus grand R2 est {v:3.3f}")
print(f"La variable la plus importante est la variable {ind+1}")


In [ ]:
def ma_reg(X,y):
    '''
    X : numpy array de dimention n x p
    y : numpy array de dimention n
    '''
    import numpy as np
    
    n,p = X.shape
    m = np.prod(y.shape)
    if n != m:
        raise Exception('X doit etre une matrice de n lignes et p colonnes et y un vecteur de n lignes')
        
    a = np.linalg.solve(X.T@X,X.T@y)
    z = X@a
    e = y - z # z - y
    s2 = np.sum(e**2)/(n-p)
    SCT = np.sum((y-np.mean(y))**2)
    SCE = np.sum(e**2)
    R2 = 1 - SCE/SCT
    H = X@np.linalg.solve(X.T@X,X.T)  # plus stable et plus rapide
    h = np.diag(H)
    c = h/((1-h)**2)*(e**2)/(p*s2)
    
    dv = np.stack([e, h, c])
    
    return a, s2, R2, dv

In [ ]:
for i in range(p):
    Xn = np.stack([X[:,i], np.ones((n,))], axis=-1)
    # calculer la matrice des variables explicatives
    A[i,:], s2[i], R2[i], diagd = ma_reg(Xn,y)#  faire la regression

with np.printoptions(precision=3, suppress=True):
    print('Erreur résiduelle :',s2) 
    print('               R2 :',R2)

v = np.max(R2)
ind = np.argmax(R2)

print(f"Le plus grand R2 est {v:3.3f}")
print(f"La variable la plus importante est la variable {ind+1}")


2. Nous allons maintenant calculer l’estimation du risque statistique (le Cp de Mallows) associé à ce modèle.
    
    a. calculez la variance estimée sur le modèle complet  (Attention aux dégrès de libertés)

In [ ]:
X_reg= np.hstack([X, np.ones((n,1))])
a_complet,s2_complet, R2_complet, _ = ma_reg(X_reg,y)

z = X_reg @ a_complet
e = y-z
#e.T@e  = \sum e_i ² 
s2_r = ((e.T@e)/(n-p-1))
print(s2_complet,s2_r)

In [ ]:
s2_r = ...

b. calculez le $C_p$ du meilleur modèle à une seule variable

In [ ]:
p0 = 2
X_best_1 = np.hstack([X[:,ind].reshape(-1,1), np.ones((n,1))])
A_best_1 = A[ind,:]
z_0 = X_best_1 @ A_best_1
e_0 = y-z_0
Cp_1variable = (1/s2_r) * (e_0.T@e_0) - n + 2 * p0
print(Cp_1variable)

In [ ]:
Cp_1variable = ...

3. Nous allons maintenant trouver quelles sont les deux variables optimales au sens du $C_p$ 

    a. combien de modèles possible avec deux variables ?  Attention, l'ordre des variables n'a pas d'importance. 

In [ ]:
nb_modeles = (p*(p-1))/2
nb_modeles

In [ ]:
nb_modeles = ...

b. Calculez le $C_p$ de chacun de ces modèles

In [ ]:
s2_2_var = np.ones((p,p))*np.inf
r2_2_var = np.ones((p,p))*np.inf
for i in range(p):
    for j in range(i+1,p):
        Xn = np.stack([X[:,i],X[:,j], np.ones((n,))], axis=-1)
        _, s2_2_var[i,j], r2_2_var[i,j], diagd = ma_reg(Xn,y)

with np.printoptions(precision=2,suppress=True):
    print(s2_2_var)
    print(r2_2_var)
    
p0 = 3    
Cp_2variable = ((s2_2_var*(n-p0))/s2_r) - n + 2 * p0
with np.printoptions(precision=2,suppress=True):
    print(Cp_2variable)
    

best_ind_2 = np.argmin(Cp_2variable)
best_cp_2 = Cp_2variable[np.unravel_index(best_ind_2, Cp_2variable.shape)]

4. Estimer le meilleur modèle au sens du $C_p$ par *forward* sélection. 

N'hésitez pas à réfléchir à l'algorithme sur une feuille de papier auparavant. 

In [ ]:
# vide -> on rajoute la meilleure variable 
p=7
var_in = [] # variables selectionnées
var_out = [x for x in range(p)] # variables candidates 
R2_all_models = []
Cp = [] # critere final pour le meilleur modele

#Calcul du s2 modele complet
X_complet = np.c_[X, np.ones(y.shape)]
_, s2_complet, _, _ = ma_reg(X_complet,y) 

# p tours de boucle pour ajouter p variables au fur et à mesure
for i in range(p):
    # parcours des variables restantes à ajouter
    s2_i = []
    R2_i = []
    for j in range(len(var_out)): # test des variables candidates
        #Creation du jeu de données avec X[:,var_out[j]] en plus de X[:,var_in] 
        liste_variables_courante = var_in + [var_out[j]]
        X_courant = X[:,liste_variables_courante]
        #Ajout des 1
        X_courant = np.concatenate([X_courant, np.ones((len(X_courant), 1))], axis=1)
        
        #Calcul de la regression, sauvegarde des résultats
        _, s2_courant, R2_courant, _ = ma_reg(X_courant,y) 
        s2_i.append(s2_courant)
        R2_i.append(R2_courant)

    #On récupère le meilleur modele (s2, R2 et Cp sont équivalents pour un même nombre de variables)
    v = np.min(s2_i)
    ind  = np.argmin(s2_i)
    R2_all_models.append(R2_i[ind])
    pi = X_courant.shape[1] # 
    #Calcul et sauvegarde du Cp pour choix final
    Cp.append((n-pi)*v/s2_complet - n + 2*pi)
    print(f"Variable gagnante pour le tour {i} : {var_out[ind]} avec un R2 de {R2_i[ind]} et un Cp de {Cp[-1]}")
    # Mise à jour de var_in et var_out
    var_in = var_in + [var_out[ind]]
    var_out.remove(var_out[ind])


In [ ]:
import matplotlib.pyplot as plt
plt.plot(range(p),Cp)
#plt.xlabel = var_in

5\. **Bonus** Estimer le meilleur modèle au sens du $C_p$ par *backward* sélection